# Ở file này ta sẽ lấy dữ liệu từ `https://mobilecity.vn/`


Cấu trúc HTML của 2 trang web Cellphones và Mobilecity không giống nhau nên cần cách tiếp cận cào dữ liệu khác nhau


# Tải các thư viện cần thiết

Nếu chưa cài đặt
Tương tự như Cellphones, vì ở đây ta cần tương tác với trang web để có thể lấy được dữ liệu nên ta sẽ sử dụng thư viện `selenium` để điều khiển trình duyệt tự động. Ta cũng cần cài đặt thêm thư viện `webdriver_manager` để tự động tải về driver cho trình duyệt mà ta đang sử dụng. Ở đây mình sẽ sử dụng Chrome.

```bash
pip install selenium webdriver_manager
```

```python

```


In [ ]:
%pip install selenium
%pip install webdriver_manager

# Import các thư viện cần thiết, để tiện cho kiểm tra và sửa lỗi


In [33]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
import time

In [34]:
url = "https://mobilecity.vn/dien-thoai"
btn_show_more_id = "product_view_more"

In [35]:
driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()))
driver.get(url)

# Trước hết ta cần lấy Link của trang chi tiết sản phẩm của từng sản phẩm


Giống như cellphones ta phải click button "Xem thêm" để load thêm sản phẩm đến khi không còn sản phẩm nào nữa


In [14]:
# Function to click all "Show More" buttons until none remain
def click_all_show_more(button_id, max_attempts=50):
    attempts = 0
    while attempts < max_attempts:
        try:
            # Find the button (adjust selector as needed)
            buttons = driver.find_elements(By.ID, button_id)
            if not buttons:
                print("No more 'Show More' buttons found")
                break
                
            # Scroll to button
            driver.execute_script("arguments[0].scrollIntoView({block: 'center'});", buttons[0])
            time.sleep(1)
            
            # Click using JavaScript (bypasses visibility requirements)
            driver.execute_script("arguments[0].click();", buttons[0])
            
            print(f"Clicked 'Show More' button: {attempts+1} times")
            attempts += 1
            
            # Wait for new content to load
            time.sleep(3)
        except Exception as e:
            print(f"Error: {e}")
            break

In [15]:
# Wait until the button is clickable
wait = WebDriverWait(driver, 10)
button = wait.until(EC.element_to_be_clickable((By.ID, btn_show_more_id)))
click_all_show_more(btn_show_more_id, max_attempts=200)


Clicked 'Show More' button: 1 times
Clicked 'Show More' button: 2 times
Clicked 'Show More' button: 3 times
Clicked 'Show More' button: 4 times
Clicked 'Show More' button: 5 times
Clicked 'Show More' button: 6 times
Clicked 'Show More' button: 7 times
Clicked 'Show More' button: 8 times
Clicked 'Show More' button: 9 times
Clicked 'Show More' button: 10 times
Clicked 'Show More' button: 11 times
Clicked 'Show More' button: 12 times
Clicked 'Show More' button: 13 times
Clicked 'Show More' button: 14 times
Clicked 'Show More' button: 15 times
Clicked 'Show More' button: 16 times
Clicked 'Show More' button: 17 times
Clicked 'Show More' button: 18 times
Clicked 'Show More' button: 19 times
Clicked 'Show More' button: 20 times
Clicked 'Show More' button: 21 times
Clicked 'Show More' button: 22 times
Clicked 'Show More' button: 23 times
Clicked 'Show More' button: 24 times
Clicked 'Show More' button: 25 times
Clicked 'Show More' button: 26 times
Clicked 'Show More' button: 27 times
Clicked 'S

KeyboardInterrupt: 

Ta sẽ lấy link của sản phẩm bằng cách trích xuất từ HTML, và điện thoại mà nhóm hướng đến là điện thoại mới nên sẽ bỏ qua các thẻ điện thoại cũ, điện thoại giảm giá theo % hoặc điện thoại chưa có giá cụ thể


In [21]:
import numpy as np
from selenium.webdriver.common.by import By

def extract_filtered_product_links(driver):
    """
    Trích xuất links sản phẩm với các điều kiện:
    - Tên không chứa '%' hoặc 'cũ'
    - Giá khác 'Liên hệ'
    
    Returns:
        np.ndarray: Mảng các URL sản phẩm đạt điều kiện
    """
    # Tìm tất cả các container sản phẩm
    product_containers = driver.find_elements(By.CSS_SELECTOR, ".product-item-left")
    print(f"Tổng số sản phẩm tìm thấy: {len(product_containers)}")
    
    filtered_links = []
    
    for product in product_containers:
        try:
            # Tìm tên và link sản phẩm
            name_element = product.find_element(By.CSS_SELECTOR, "p.name a")
            product_name = name_element.text.strip()
            product_link = name_element.get_attribute("href")
            
            # Tìm giá sản phẩm
            price_element = product.find_element(By.CSS_SELECTOR, "p.price")
            product_price = price_element.text.strip()
            
            # Kiểm tra điều kiện lọc
            has_percent = "%" in product_name
            has_cu = "cũ" in product_name.lower()
            is_contact_price = product_price == "Liên hệ"
            
            # Chỉ lấy sản phẩm thỏa mãn điều kiện
            if not has_percent and not has_cu and not is_contact_price:
                filtered_links.append(product_link)
                print(f"Tìm thấy sản phẩm hợp lệ: {product_name} - {product_price}")
        except Exception as e:
            print(f"Lỗi khi xử lý một sản phẩm: {e}")
    
    # Chuyển đổi danh sách thành numpy array
    links_array = np.array(filtered_links)
    
    print(f"Đã lọc được {len(links_array)} sản phẩm thỏa mãn điều kiện")
    return links_array

# Sử dụng hàm
filtered_product_links = extract_filtered_product_links(driver)

# In thông tin kết quả
print(f"Số lượng link đã lọc: {len(filtered_product_links)}")
print("5 link đầu tiên:")
if len(filtered_product_links) > 0:
    for i, link in enumerate(filtered_product_links[:5]):
        print(f"{i+1}. {link}")

Tổng số sản phẩm tìm thấy: 1550
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi 12C (Helio G85) - 1.650.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 12 5G (Có tiếng Việt, Snapdragon 4 Gen 1) - 2.550.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi 14C Chính hãng (Helio G81 Ultra) siêu rẻ - 2.650.000 ₫
Tìm thấy sản phẩm hợp lệ: OPPO A3x 5G (Dùng như máy Chính hãng) - 2.700.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 13 5G China (Dimensity 6080) - 2.950.000 ₫
Tìm thấy sản phẩm hợp lệ: Vivo iQOO Z9x 5G (pin 6000mAh) - 3.350.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 13 Chính hãng DGW (Snapdragon 685) - 3.650.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 12 Discovery Edition - 3.950.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi REDMI Note 14 Chính hãng (Helio G99 Ultra) - 4.000.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 14 5G (Dimensity 7025 Ultra) - 4.050.000 ₫
Tìm thấy sản phẩm hợp lệ: Xiaomi Redmi Note 13 Pro 5G (Snapdragon 7s Gen 2) - 4.150.000 ₫
Tìm thấy sản phẩm hợp lệ: Vivo

Lưu lại link vào file csv sau khi đã cào xong


In [22]:
import csv

# Write the links to a CSV file
with open("product_links_mobilecity.csv", "w", newline="") as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["Product Link"])
    writer.writerows([[link] for link in filtered_product_links])

# Các hàm để lấy dữ liệu khi vào trang chi tiết sản phẩm


Từ các Link đã lấy, ta sẽ vào từng trang chi tiết sản phẩm để lấy các thông tin như sau:

-   Tên sản phẩm
-   Giá sản phẩm
-   Thông tin thông số kỹ thuật


In [ ]:
import json
import time
import traceback
from selenium.webdriver.common.by import By
from selenium.webdriver.remote.webdriver import WebDriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException, ElementNotInteractableException, StaleElementReferenceException
from typing import Dict, Optional, Any, List

def execute_js(driver, script):
    return driver.execute_script(script)

def extract_product_common_info(driver: WebDriver, product_link: str) -> Dict[str, Any]:
    """
    Extract common product information from a product page with improved robustness.
    
    Parameters:
    - driver: Selenium WebDriver instance
    - product_link: URL of the product page
    
    Returns:
    - Dictionary containing product information
    """
    # Initialize result dictionary with default values
    product_data = {
        "url": product_link,
        "name": "",
        "price": "",
        "specifications": []
    }
    
    try:
        print(f"Extracting data from: {product_link}")
        driver.get(product_link)
        time.sleep(1)
        
        # CHIẾN LƯỢC 1: Lấy tên sản phẩm (thử nhiều selector)
        try:
            name_selectors = [
                ".product-title h1.title", 
                ".product-title h1",
                "h1.title",
                ".box-product-name h1",
                ".product-name h1"
            ]
            
            for selector in name_selectors:
                try:
                    name_element = driver.find_element(By.CSS_SELECTOR, selector)
                    name = name_element.text.strip()
                    if name:
                        product_data["name"] = name.replace("Điện thoại", "").replace("(Chính hãng)", "").strip()
                        print(f"Found product name: {name}")
                        break
                except (NoSuchElementException, StaleElementReferenceException):
                    continue
        except Exception as e:
            print(f"Error getting product name: {e}")


        # CHIẾN LƯỢC 2: Lấy giá sản phẩm (thử nhiều selector)
        try:
            price_selectors = [
                "div.price-product price",
                "div.price-product p.price",
                ".price-product .price",
                ".box-price .price",
                ".price strong"
            ]
            
            for selector in price_selectors:
                try:
                    price_element = driver.find_element(By.CSS_SELECTOR, selector)
                    price = price_element.text.strip()
                    if price:
                        product_data["price"] = price.strip().replace("₫", "").replace(".", "").strip()
                        print(f"Found product price: {price}")
                        break
                except (NoSuchElementException, StaleElementReferenceException):
                    continue
        except Exception as e:
            print(f"Error getting product price: {e}")
        
        # CHIẾN LƯỢC 3: Trích xuất thông số kỹ thuật qua nhiều cách
        specifications = []
        spec_extracted = False
        
        # Cách 1: Thử click vào button và lấy từ modal
        try:
            # Scroll xuống trang để button xuất hiện
            for scroll_position in [250, 500, 750, 1000, 1250]:
                try:
                    execute_js(driver, f"window.scrollTo(0, {scroll_position});")
                    time.sleep(0.5)
                    
                    # Thử tìm và click button bằng nhiều cách
                    button_clicked = False
                    
                    # Cách 1: Sử dụng selector trực tiếp
                    try:
                        button_selectors = [
                            "#product-show-lightbox",
                            "span.product-show-lightbox",
                            "span:contains('Xem thêm cấu hình chi tiết')"
                        ]
                        
                        for selector in button_selectors:
                            try:
                                click_script = f"""
                                    var btn = document.querySelector('{selector}');
                                    if(btn) {{
                                        btn.scrollIntoView({{block: 'center'}});
                                        btn.click();
                                        return true;
                                    }}
                                    return false;
                                """
                                button_clicked = execute_js(driver, click_script)
                                if button_clicked:
                                    print(f"Clicked technical button with selector: {selector}")
                                    time.sleep(1.5)
                                    break
                            except:
                                continue
                    except Exception as e:
                        print(f"Error clicking button with selector: {e}")
                    
                    # Cách 2: Tìm bằng XPath với nội dung text
                    if not button_clicked:
                        try:
                            xpath_patterns = [
                                "//button[contains(text(), 'Xem cấu hình chi tiết')]",
                                "//a[contains(text(), 'Xem cấu hình chi tiết')]",
                                "//a[contains(text(), 'Thông số kỹ thuật')]",
                                "//a[contains(text(), 'cấu hình')]",
                                "//a[contains(@onclick, 'showLightbox')]"
                            ]
                            
                            for xpath in xpath_patterns:
                                try:
                                    button = driver.find_element(By.XPATH, xpath)
                                    if button.is_displayed():
                                        execute_js(driver, "arguments[0].scrollIntoView({block: 'center'});", button)
                                        time.sleep(0.5)
                                        execute_js(driver, "arguments[0].click();", button)
                                        button_clicked = True
                                        print(f"Clicked technical button with xpath: {xpath}")
                                        time.sleep(1.5)
                                        break
                                except:
                                    continue
                        except Exception as e:
                            print(f"Error clicking button with xpath: {e}")
                    
                    if button_clicked:
                        # Đợi modal hiển thị
                        try:
                            modal_selectors = [
                                ".product-lightbox-content",
                                "div.product-lightbox-content",
                            ]
                            
                            modal_found = False
                            for selector in modal_selectors:
                                try:
                                    WebDriverWait(driver, 3).until(
                                        EC.visibility_of_element_located((By.CSS_SELECTOR, selector))
                                    )
                                    print(f"Modal found with selector: {selector}")
                                    modal_found = True
                                    
                                    # Trích xuất dữ liệu từ modal với JS - Thêm code cho cấu trúc MobileCity
                                    js_script = """
                                    function extractSpecifications() {
                                        // MobileCity: Thử với cấu trúc product-lightbox-content
                                        const mobileCityTable = document.querySelector('.product-lightbox-content table');
                                        if (mobileCityTable) {
                                            const rows = Array.from(mobileCityTable.querySelectorAll('tr'));
                                            let result = [];
                                            let currentCategory = null;
                                            let currentDetails = {};
                                            
                                            for (const row of rows) {
                                                const cells = row.querySelectorAll('td');
                                                
                                                // Nếu có một cell với colspan=2, đây là tiêu đề danh mục
                                                if (cells.length === 1 && cells[0].getAttribute('colspan') === '2') {
                                                    // Lưu danh mục hiện tại nếu có
                                                    if (currentCategory && Object.keys(currentDetails).length > 0) {
                                                        result.push({
                                                            category: currentCategory,
                                                            details: {...currentDetails}
                                                        });
                                                    }
                                                    
                                                    // Bắt đầu danh mục mới
                                                    currentCategory = cells[0].innerText.trim();
                                                    currentDetails = {};
                                                } 
                                                // Nếu có 2 cells, đây là cặp key-value
                                                else if (cells.length >= 2) {
                                                    const key = cells[0].innerText.trim().replace(':', '');
                                                    let value = cells[1].innerText.trim();
                                                    
                                                    // Xử lý giá trị nhiều dòng
                                                    if (value.includes('\\n')) {
                                                        value = value.split('\\n')
                                                            .map(v => v.trim())
                                                            .filter(v => v !== "");
                                                    }
                                                    
                                                    // Thêm vào danh mục hiện tại
                                                    if (key && (value !== "" || (Array.isArray(value) && value.length > 0))) {
                                                        currentDetails[key] = value;
                                                    }
                                                }
                                            }
                                            
                                            // Thêm danh mục cuối cùng
                                            if (currentCategory && Object.keys(currentDetails).length > 0) {
                                                result.push({
                                                    category: currentCategory,
                                                    details: {...currentDetails}
                                                });
                                            }
                                            
                                            return result.length > 0 ? result : null;
                                        }
                                        
                                        const ul = document.querySelector('ul.technical-content-modal');
                                        if (ul) {
                                            const items = Array.from(ul.querySelectorAll('li.technical-content-modal-item'));
                                            const result = items.map(item => {
                                                const titleElem = item.querySelector('p.title');
                                                const category = titleElem ? titleElem.innerText.trim() : "";
                                                const specDivs = item.querySelectorAll('div.modal-item-description > div');
                                                const details = {};
                                                
                                                specDivs.forEach(div => {
                                                    const keyElem = div.querySelector('p');
                                                    const valueElem = div.querySelector('div');
                                                    if(keyElem && valueElem) {
                                                        const key = keyElem.innerText.trim();
                                                        let value = valueElem.innerText.trim();
                                                        if(value.indexOf('\\n') !== -1) {
                                                            value = value.split('\\n').map(s => s.trim()).filter(s => s !== "");
                                                        }
                                                        details[key] = value;
                                                    }
                                                });
                                                return { category: category, details: details };
                                            });
                                            
                                            return result.length > 0 ? result : null;
                                        }
                                        
                                        // Không tìm thấy dữ liệu nào
                                        return null;
                                    }
                                    
                                    const specs = extractSpecifications();
                                    return JSON.stringify(specs);
                                    """
                                    
                                    json_data = execute_js(driver, js_script)
                                    extracted_specs = json.loads(json_data) if json_data and json_data != "null" else None
                                    
                                    if extracted_specs and len(extracted_specs) > 0:
                                        specifications = extracted_specs
                                        spec_extracted = True
                                        print(f"Extracted {len(extracted_specs)} specification categories from modal")
                                        break
                                except Exception as e:
                                    print(f"Error with selector {selector}: {e}")
                                    continue
                            
                            if modal_found and spec_extracted:
                                break
                        except Exception as e:
                            print(f"Error extracting from modal: {e}")
                except Exception as e:
                    print(f"Error during modal interaction at scroll {scroll_position}: {e}")
                    
                if spec_extracted:
                    break
        except Exception as e:
            print(f"Error in modal extraction strategy: {e}")
        
        # Cách 2: Tìm thông số kỹ thuật trực tiếp từ trang
        if not spec_extracted:
            try:
                print("Trying direct page extraction")
                js_script = """
                function extractSpecificationsFromPage() {
                    // Tìm bảng thông số kỹ thuật trực tiếp trên trang
                    const tables = document.querySelectorAll('.product-detail table, .product-info table, .product-specification table');
                    
                    if (tables.length > 0) {
                        let result = [];
                        
                        tables.forEach(table => {
                            const rows = table.querySelectorAll('tr');
                            if (rows.length === 0) return;
                            
                            let currentCategory = "Thông số kỹ thuật";
                            let currentDetails = {};
                            
                            rows.forEach(row => {
                                const cells = row.querySelectorAll('td');
                                
                                // Kiểm tra nếu là hàng tiêu đề danh mục
                                if (cells.length === 1 && cells[0].getAttribute('colspan') === '2') {
                                    // Lưu danh mục trước đó nếu có
                                    if (Object.keys(currentDetails).length > 0) {
                                        result.push({
                                            category: currentCategory,
                                            details: {...currentDetails}
                                        });
                                    }
                                    
                                    // Thiết lập danh mục mới
                                    currentCategory = cells[0].innerText.trim();
                                    currentDetails = {};
                                } 
                                // Nếu là hàng thông số bình thường
                                else if (cells.length >= 2) {
                                    const key = cells[0].innerText.trim().replace(':', '');
                                    let value = cells[1].innerText.trim();
                                    
                                    // Xử lý giá trị nhiều dòng
                                    if (value.includes('\\n')) {
                                        value = value.split('\\n')
                                            .map(v => v.trim())
                                            .filter(v => v !== "");
                                    }
                                    
                                    if (key && (value !== "" || Array.isArray(value) && value.length > 0)) {
                                        currentDetails[key] = value;
                                    }
                                }
                            });
                            
                            // Thêm danh mục cuối cùng
                            if (Object.keys(currentDetails).length > 0) {
                                result.push({
                                    category: currentCategory,
                                    details: {...currentDetails}
                                });
                            }
                        });
                        
                        return result;
                    }
                    
                    return [];
                }
                
                return JSON.stringify(extractSpecificationsFromPage());
                """
                
                json_data = execute_js(driver, js_script)
                extracted_specs = json.loads(json_data) if json_data and json_data != "null" else None
                
                if extracted_specs and len(extracted_specs) > 0:
                    specifications = extracted_specs
                    spec_extracted = True
                    print(f"Extracted {len(extracted_specs)} specification categories directly from page")
            except Exception as e:
                print(f"Error in direct page extraction: {e}")
        
        # Lưu thông số vào kết quả
        if specifications:
            product_data["specifications"] = specifications
            
                
    except Exception as e:
        print(f"Error during extraction: {traceback.format_exc()}")
    
    print(f"product name common data: ", product_data)
    return product_data

In [50]:
extract_product_common_info(driver, filtered_product_links[0])

Extracting data from: https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html
Found product name: Điện thoại Xiaomi Redmi 12C (Helio G85)
Found product price: 1.650.000 ₫
Clicked technical button with selector: #product-show-lightbox
Modal found with selector: .product-lightbox-content
Extracted 9 specification categories from modal
product name common data:  {'url': 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html', 'name': 'Xiaomi Redmi 12C (Helio G85)', 'price': '1650000', 'specifications': [{'category': 'Thông tin chung', 'details': {'Hệ điều hành': 'Android 12, MIUI 13', 'Ngôn ngữ': 'Đa ngôn ngữ'}}, {'category': 'Màn hình', 'details': {'Loại màn hình': 'IPS LCD', 'Màu màn hình': '16 triệu màu', 'Chuẩn màn hình': ['IPS LCD, 500 nits (typ)', '6.71 inches, HD+ (720 x 1650 pixels)'], 'Độ phân giải': '720 x 1650 pixels', 'Màn hình rộng': '6.71 inches', 'Công nghệ cảm ứng': 'Cảm ứng điện dung đa điểm'}}, {'category': 'Chụp hình & Quay phim', 'details': {'Camera

{'url': 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html',
 'name': 'Xiaomi Redmi 12C (Helio G85)',
 'price': '1650000',
 'specifications': [{'category': 'Thông tin chung',
   'details': {'Hệ điều hành': 'Android 12, MIUI 13',
    'Ngôn ngữ': 'Đa ngôn ngữ'}},
  {'category': 'Màn hình',
   'details': {'Loại màn hình': 'IPS LCD',
    'Màu màn hình': '16 triệu màu',
    'Chuẩn màn hình': ['IPS LCD, 500 nits (typ)',
     '6.71 inches, HD+ (720 x 1650 pixels)'],
    'Độ phân giải': '720 x 1650 pixels',
    'Màn hình rộng': '6.71 inches',
    'Công nghệ cảm ứng': 'Cảm ứng điện dung đa điểm'}},
  {'category': 'Chụp hình & Quay phim',
   'details': {'Camera sau': ['50 MP (góc rộng), PDAF',
     '0.08 MP (độ sâu)',
     'Quay phim: 1080p@30fps'],
    'Camera trước': ['5 MP', 'Quay phim: 1080p@30fps'],
    'Đèn Flash': 'Có',
    'Tính năng camera': 'LED flash, HDR',
    'Quay phim': '1080p@30fps',
    'Videocall': 'Có'}},
  {'category': 'CPU & RAM',
   'details': {'Tốc độ CPU': 

In [51]:
def getAndSaveProductInfo(driver: WebDriver, product_link: str) -> Dict[str, Any]:
    """
    Lấy thông tin sản phẩm từ trang product_link bằng cách cào thông tin common và variant, sau đó merge lại thành 1 dict.
    
    Returns:
    - Dictionary chứa thông tin sản phẩm, bao gồm:
         - url, specifications, variant_prices
    """
    driver.get(product_link)
    time.sleep(2)
    
    product_common_data = extract_product_common_info(driver, product_link)
    if product_common_data is None:
        product_common_data = {"url": product_link, "specifications": {}}
    
    print("product name common data: ", product_common_data)
    file_name = product_common_data["name"].replace(" ", "_").replace("/", "_") + ".json"
    
    with open("json/" + file_name, "w", encoding="utf-8") as f:
        json.dump(product_common_data, f, ensure_ascii=False, indent=4)
        
    return product_common_data

In [52]:
import csv
product_links = []
with open("./product_links_mobilecity.csv", "r") as f:
    reader = csv.reader(f)
    next(reader)  # Skip header
    for row in reader:
        product_links.append(row[0])
product_links[:5]

['https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html',
 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-note-12-5g-snapdragon-4-gen-1.html',
 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-14c-helio-g81ultra.html',
 'https://mobilecity.vn/dien-thoai/oppo-a3x-5g-dimensity-6300.html',
 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-note-13-gia-re.html']

In [ ]:
import concurrent.futures
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
from webdriver_manager.chrome import ChromeDriverManager
from typing import Dict, List, Any
import time
import json
import os
import random
from tqdm import tqdm

def crawl_products_multithreaded(product_links: List[str], max_workers: int = 5, 
                                 batch_size: int = 10, delay_between_batches: int = 3) -> List[Dict[str, Any]]:
    """
    Cào dữ liệu sản phẩm đa luồng từ danh sách các liên kết sản phẩm.
    
    Nếu một liên kết gặp lỗi, sẽ được thêm vào cuối danh sách để xử lý lại tuần tự sau.
    
    Args:
        product_links: Danh sách các URL sản phẩm cần cào
        max_workers: Số lượng luồng tối đa chạy đồng thời
        batch_size: Kích thước mỗi batch để tránh quá tải
        delay_between_batches: Thời gian chờ giữa các batch (giây)
    
    Returns:
        Danh sách các dictionary chứa thông tin sản phẩm
    """
    # Đảm bảo thư mục json tồn tại
    os.makedirs("json", exist_ok=True)
    
    results = []
    retry_links = []  # Danh sách các liên kết cần thử lại
    
    # Chia danh sách sản phẩm thành các batch nhỏ hơn
    batches = [product_links[i:i+batch_size] for i in range(0, len(product_links), batch_size)]
    
    print(f"Chia thành {len(batches)} batch, mỗi batch {batch_size} sản phẩm")
    
    def worker(link):
        try:
            # Khởi tạo driver riêng cho mỗi thread
            options = Options()
            options.add_argument("--headless")  # Chạy ngầm không hiển thị UI
            options.add_argument("--disable-gpu")
            options.add_argument("--no-sandbox")
            options.add_argument("--disable-dev-shm-usage")
            
            driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), 
                                      options=options)
            
            try:
                # Random Sleep trước mỗi request để tránh bị chặn
                time.sleep(random.uniform(1, 3))
                # Gọi hàm getAndSaveProductInfo để cào dữ liệu
                result = getAndSaveProductInfo(driver, link)
                return result
            finally:
                # Đảm bảo đóng driver sau khi sử dụng
                driver.quit()
                
        except Exception as e:
            error_msg = f"Lỗi khi xử lý link {link}: {str(e)}"
            print(error_msg)
            return {"url": link, "error": str(e), "specifications": {}, "variant_prices": []}
    
    # Xử lý theo từng batch với đa luồng
    for batch_idx, batch in enumerate(batches):
        print(f"Đang xử lý batch {batch_idx+1}/{len(batches)}")
        batch_results = []
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
            futures = {executor.submit(worker, link): link for link in batch}
            for future in tqdm(concurrent.futures.as_completed(futures), total=len(batch), 
                              desc=f"Batch {batch_idx+1}"):
                link = futures[future]
                try:
                    result = future.result()
                    batch_results.append(result)
                except Exception as e:
                    # Nếu có lỗi ngoài dự tính, báo lỗi và tiếp tục
                    print(f"Lỗi khi lấy kết quả cho {link}: {str(e)}")
                    batch_results.append({"url": link, "error": str(e), "specifications": {}, "variant_prices": []})
        
        results.extend(batch_results)
        print(f"Đã cào {len(batch_results)}/{len(batch)} sản phẩm từ batch {batch_idx+1}")
        print(f"Tổng số sản phẩm đã cào: {len(results)}/{len(product_links)}")
        
        if batch_idx < len(batches) - 1:
            print(f"Chờ {delay_between_batches} giây trước khi xử lý batch tiếp theo...")
            time.sleep(delay_between_batches)
    
    # Xử lý các liên kết lỗi sau khi đa luồng bằng cách tuần tự
    # Nếu một liên kết lỗi, thêm nó vào cuối danh sách retry_links để thử lại sau
    retry_links = [result["url"] for result in results if result.get("error")]
    attempt = 1
    while retry_links:
        print(f"\nBắt đầu xử lý lại {len(retry_links)} liên kết lỗi (Lần thử: {attempt})")
        current_retry = retry_links.copy()
        retry_links = []  # reset danh sách lỗi
        
        for link in tqdm(current_retry, desc=f"Retry attempt {attempt}"):
            try:
                options = Options()
                options.add_argument("--headless")
                options.add_argument("--disable-gpu")
                options.add_argument("--no-sandbox")
                options.add_argument("--disable-dev-shm-usage")
                
                driver = webdriver.Chrome(service=Service(ChromeDriverManager().install()), 
                                          options=options)
                try:
                    # Cho phép load chậm hơn, không thêm độ trễ ngẫu nhiên
                    time.sleep(2)
                    result = getAndSaveProductInfo(driver, link)
                    # Cập nhật kết quả mới vào danh sách results:
                    # Tìm vị trí của kết quả cũ và thay thế
                    for idx, r in enumerate(results):
                        if r["url"] == link:
                            results[idx] = result
                            break
                finally:
                    driver.quit()
            except Exception as e:
                print(f"Lỗi khi xử lý lại link {link}: {str(e)}")
                # Nếu lỗi vẫn xảy ra, thêm link vào cuối danh sách để thử lại sau
                retry_links.append(link)
        if retry_links:
            print(f"Vẫn còn {len(retry_links)} liên kết lỗi, chờ 10 giây trước khi thử lại...")
            time.sleep(10)
        attempt += 1

    # Lưu tất cả kết quả vào một file JSON
    try:
        with open("all_products_mobilecity.json", "w", encoding="utf-8") as f:
            json.dump(results, f, indent=4, ensure_ascii=False)
        print(f"Đã lưu tất cả {len(results)} kết quả vào all_products.json")
    except Exception as e:
        print(f"Lỗi khi lưu all_products.json: {str(e)}")
    
    return results

# Ví dụ sử dụng:
if __name__ == "__main__":
    # product_links cần được định nghĩa trước đó (ví dụ: danh sách các URL sản phẩm)
    # Ví dụ: product_links = ["http://example.com/product1", "http://example.com/product2", ...]
    results = crawl_products_multithreaded(
        product_links=product_links,
        max_workers=4,      # Giảm xuống 2 luồng
        batch_size=5,       # Giảm xuống 2 sản phẩm/batch
        delay_between_batches=20  # Tăng đợi giữa các batch
    )
    
    print(f"Hoàn thành cào dữ liệu cho {len(results)} sản phẩm")


Chia thành 194 batch, mỗi batch 5 sản phẩm
Đang xử lý batch 1/194


Batch 1:   0%|          | 0/5 [00:00<?, ?it/s]

Extracting data from: https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html
Extracting data from: https://mobilecity.vn/dien-thoai/xiaomi-redmi-note-12-5g-snapdragon-4-gen-1.html
Found product name: Điện thoại Xiaomi Redmi 12C (Helio G85)
Found product price: 1.650.000 ₫
Clicked technical button with selector: #product-show-lightbox
Found product name: Điện thoại Xiaomi Redmi Note 12 5G (Có tiếng Việt, Snapdragon 4 Gen 1)
Found product price: 2.550.000 ₫
Clicked technical button with selector: #product-show-lightbox
Modal found with selector: .product-lightbox-content
Extracted 9 specification categories from modal
product name common data:  {'url': 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-12c-helio-g85.html', 'name': 'Xiaomi Redmi 12C (Helio G85)', 'price': '1650000', 'specifications': [{'category': 'Thông tin chung', 'details': {'Hệ điều hành': 'Android 12, MIUI 13', 'Ngôn ngữ': 'Đa ngôn ngữ'}}, {'category': 'Màn hình', 'details': {'Loại màn hình': 'IPS LCD', 'Màu mà

Batch 1:  60%|██████    | 3/5 [00:23<00:13,  6.75s/it]

Lỗi khi xử lý link https://mobilecity.vn/dien-thoai/xiaomi-redmi-14c-helio-g81ultra.html: HTTPSConnectionPool(host='googlechromelabs.github.io', port=443): Read timed out. (read timeout=None)
Extracting data from: https://mobilecity.vn/dien-thoai/xiaomi-redmi-note-13-gia-re.html
Found product name: Điện thoại Xiaomi Redmi Note 13 5G China (Dimensity 6080)
Found product price: 2.950.000 ₫
Clicked technical button with selector: #product-show-lightbox
Modal found with selector: .product-lightbox-content
Extracted 9 specification categories from modal
product name common data:  {'url': 'https://mobilecity.vn/dien-thoai/xiaomi-redmi-note-13-gia-re.html', 'name': 'Xiaomi Redmi Note 13 5G China (Dimensity 6080)', 'price': '2950000', 'specifications': [{'category': 'Thông tin chung', 'details': {'Hệ điều hành': 'Android 13, MIUI 14', 'Ngôn ngữ': 'Đa ngôn ngữ'}}, {'category': 'Màn hình', 'details': {'Loại màn hình': 'AMOLED', 'Màu màn hình': '1 tỷ màu', 'Chuẩn màn hình': ['AMOLED, 1 tỷ màu, 12

...

Extracting data from: https://mobilecity.vn/dien-thoai/iphone-14-pro-max.html
Found product name: Điện thoại iPhone 14 Pro Max Chính hãng VN/A (128GB | 256GB | 512GB)
Found product price: 24.490.000 ₫
Clicked technical button with selector: #product-show-lightbox
Modal found with selector: .product-lightbox-content
Extracted 9 specification categories from modal
product name common data:  {'url': 'https://mobilecity.vn/dien-thoai/iphone-14-pro-max.html', 'name': 'iPhone 14 Pro Max Chính hãng VN/A (128GB | 256GB | 512GB)', 'price': '24490000', 'specifications': [{'category': 'Thông tin chung', 'details': {'Hệ điều hành': 'iOS 16', 'Ngôn ngữ': 'Tiếng Việt, Đa ngôn ngữ'}}, {'category': 'Màn hình', 'details': {'Loại màn hình': 'Super Retina XDR OLED', 'Màu màn hình': '16 triệu màu', 'Chuẩn màn hình': ['LTPO Super Retina XDR OLED, 120Hz, HDR10, Dolby Vision', '6.7 inches, Full HD+ (1290 x 2796 pixels)', 'Thủy tinh gốm chống xước, lớp phủ oleophobic', 'Always-On display'], 'Độ phân giải': '1

Retry attempt 347: 100%|██████████| 1/1 [00:16<00:00, 16.52s/it]

Lỗi khi xử lý lại link https://mobilecity.vn/dien-thoai/iphone-14-pro-max.html: [Errno 22] Invalid argument: 'json/iPhone_14_Pro_Max_Chính_hãng_VN_A_(128GB_|_256GB_|_512GB).json'
Vẫn còn 1 liên kết lỗi, chờ 10 giây trước khi thử lại...



Bắt đầu xử lý lại 1 liên kết lỗi (Lần thử: 348)


Retry attempt 348:   0%|          | 0/1 [00:20<?, ?it/s]


# Gom kết quả


In [2]:
import os
import json

# Đường dẫn folder chứa file JSON
json_folder = "json"
results = []

# Duyệt qua tất cả các file trong folder
for filename in os.listdir(json_folder):
    if filename.endswith(".json"):
        filepath = os.path.join(json_folder, filename)
        with open(filepath, "r", encoding="utf-8") as f:
            try:
                data = json.load(f)
            except json.JSONDecodeError:
                print(f"Error parsing {filename}")
                continue
        
        # Điều kiện 1: Kiểm tra giá không phải "liên hệ" hoặc "giá liên hệ"
        price = data.get("price", "").strip()
        if price.lower() in ["liên hệ", "giá liên hệ"]:
            continue
        
        # Tiền xử lý giá: xóa ký hiệu "đ", thay dấu chấm bằng rỗng, strip 2 bên
        processed_price = price.replace("đ", "").replace(".", "").strip()
        data["price"] = processed_price
        
        # Điều kiện 2: Specifications khác null và có ít nhất 1 phần tử
        specifications = data.get("specifications")
        if not specifications or len(specifications) < 1:
            continue
        
        # Điều kiện 3: Tên sản phẩm không chứa "%" và không chứa "cũ"
        name = data.get("name", "")
        if "%" in name or "cũ" in name.lower():
            continue
        
        results.append(data)

print(f"Đã lọc được {len(results)} sản phẩm hợp lệ")
print("result[0]: ", results[0])
# Lưu kết quả vào file JSON mới
with open("filtered_products_mobilecity.json", "w", encoding="utf-8") as f:
    json.dump(results, f, ensure_ascii=False, indent=4)



Đã lọc được 1244 sản phẩm hợp lệ
result[0]:  {'url': 'https://cellphones.com.vn/asus-rog-phone-6-12gb-256gb.html', 'name': 'ASUS ROG Phone 6 12GB 256GB', 'price': '14490000', 'specifications': [{'category': 'Màn hình', 'details': {'Kích thước màn hình': '6.78 inches', 'Công nghệ màn hình': 'AMOLED', 'Độ phân giải màn hình': '1080 x 2448 pixels (FullHD+)', 'Tính năng màn hình': 'Corning ® Gorilla ® Glass Victus, 165Hz, Độ sáng tối đa: 1200 nits, Mật độ điểm ảnh: 395 ppi'}}, {'category': 'Camera sau', 'details': {'Camera sau': ['Camera chính: 50 MP, f/1.9', 'Camera góc siêu rộng: 13 MP', 'Camera macro: 5 MP'], 'Quay video': '8K@24fps , 4K@30/60fps', 'Tính năng camera': 'Flash LED, HDR, Trôi nhanh thời gian (Time Lapse), Quay chậm (Slow Motion)'}}, {'category': 'Camera trước', 'details': {'Camera trước': '12 MP', 'Quay video trước': '1080p@30/60fps, 720p@30/60 fps'}}, {'category': 'Vi xử lý & đồ họa', 'details': {'Chipset': 'Qualcomm ® Snapdragon ® 8+ thế hệ 1', 'GPU': 'Adreno ™ 730'}}, {

10h28 29/3 đã thử fetch lại 250 sản phẩm đầu tiên của cellphones. Ngày mai sẽ thử tiếp với 250 sản phẩm tiếp theo
